In [1]:
# Copyright 2024 Keysight Technologies Inc.

In [2]:
import trueq as tq

circuit = tq.Circuit(
    cycles=[
        tq.Cycle({(0, 1): tq.Gate.cz}),
        tq.Cycle({0: tq.Gate.h, 1: tq.Gate.h}),
        tq.Cycle({(2, 1): tq.Gate.cx}),
        tq.Cycle({(0, 1): tq.Gate.cy, 2: tq.Gate.z}),
    ]
)
circuit.draw()

DisplayWrapper(<svg xmlns="http://w...)

In [3]:
replace_pass = tq.compilation.CycleReplacement(
    target=tq.Cycle({(0, 1): tq.Gate.cz}),
    replacement=3 * [tq.Cycle({(0, 1): tq.Gate.cz})],
)
merge_pass = tq.compilation.Merge(max_sys=2)

In [4]:
replace_compiler = tq.compilation.Compiler(passes=[replace_pass])
merge_compiler = tq.compilation.Compiler(passes=[merge_pass])

In [5]:
compilation1 = replace_compiler.compile(circuit)
compilation1.draw()

DisplayWrapper(<svg xmlns="http://w...)

In [6]:
compilation2 = merge_compiler.compile(compilation1)
compilation2.draw()

DisplayWrapper(<svg xmlns="http://w...)

In [7]:
composite_compiler = tq.compilation.Compiler(passes=[replace_pass, merge_pass])

composite_compilation = composite_compiler.compile(circuit)
composite_compilation.draw()

DisplayWrapper(<svg xmlns="http://w...)

In [8]:
# define a compiler to simplify circuits
compiler1 = tq.Compiler.basic(passes=tq.Compiler.SIMPLIFY_PASSES)

# define a compiler that does randomized compiling
compiler2 = tq.Compiler.basic(passes=tq.Compiler.RC_PASSES)

# define a compiler that decomposes two-qubit gates into the specified entangling gate,
# then randomly compiles, and then converts all gates into hardware compatable gates.
# for this example, we use the maximally entangling cross-resonance gate.
passes = (
    tq.Compiler.NATIVE2Q_PASSES + tq.Compiler.RC_PASSES + tq.Compiler.HARDWARE_PASSES
)
compiler3 = tq.Compiler.basic(entangler=tq.Gate.rp("ZX", 90), passes=passes)

In [9]:
circuit = tq.Circuit(
    [{range(4): tq.Gate.h}, {(0, 1): tq.Gate.rp("ZZ", 22), (2, 3): tq.Gate.cz}]
).measure_all()
circuit

Circuit(Cycle((0,): Gate.h, (1,): Gate.h, (2,): Gate.h, (3,): Gate.h),Cycle((0, 1): Gate(ZZ), (2, 3): Gate.cz),Cycle((0,): Meas(), (1,): Meas(), (2,): Meas(), (3,): Meas(), marker=1))

In [10]:
compiler3.compile(circuit)

Circuit(Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): sx(), (1,): sx(), (2,): sx(), (3,): sx()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): sx(), (1,): sx(), (2,): sx(), (3,): sx()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0, 1): entangler(), marker=2),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): sx(), (1,): sx(), (2,): sx(), (3,): sx()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): sx(), (1,): sx(), (2,): sx(), (3,): sx()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0, 1): entangler(), (2, 3): entangler(), marker=3),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): sx(), (1,): sx(), (2,): sx(), (3,): sx()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): sx(), (1,): sx(), (2,): sx(), (3,): sx()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): Meas(), (1,): Meas(), (2,): Meas(), (3,): Meas(), marker=1))

In [11]:
b = tq.Gate.from_generators("XX", 90, "YY", 45)
config = tq.Config(
    factories=[
        tq.config.GateFactory.from_matrix("B", b),
        tq.config.GateFactory.from_hamiltonian("x90", [["X", 90]]),
        tq.config.GateFactory.from_hamiltonian("z", [["Z", "phi"]]),
    ],
    mode="ZXZXZ",
)

In [12]:
decomposer = tq.compilation.NativeDecomp(depth=2, factories=config.factories)
compiler = tq.Compiler(
    [
        tq.compilation.Merge(max_sys=2),
        tq.compilation.Parallel(decomposer),
        tq.compilation.Merge(),
        tq.compilation.Native1Q(config.factories),
        tq.compilation.RemoveEmptyCycle(),
    ]
)

In [13]:
circuit = tq.Circuit(
    [
        {range(4): tq.Gate.h},
        {(0, 1): tq.Gate.rp("ZZ", 22)},
        {(0, 1): tq.Gate.cnot, (2, 3): tq.Gate.swap},
    ]
).measure_all()
circuit

Circuit(Cycle((0,): Gate.h, (1,): Gate.h, (2,): Gate.h, (3,): Gate.h),Cycle((0, 1): Gate(ZZ)),Cycle((0, 1): Gate.cx, (2, 3): Gate.swap),Cycle((0,): Meas(), (1,): Meas(), (2,): Meas(), (3,): Meas(), marker=1))

In [14]:
compiler.compile(circuit)

Circuit(Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): x90(), (1,): x90(), (2,): x90(), (3,): x90()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): x90(), (1,): x90(), (2,): x90(), (3,): x90()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0, 1): B(), (2, 3): B()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): x90(), (1,): x90(), (2,): x90(), (3,): x90()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): x90(), (1,): x90(), (2,): x90(), (3,): x90()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0, 1): B(), (2, 3): B()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): x90(), (1,): x90(), (2,): x90(), (3,): x90()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): x90(), (1,): x90(), (2,): x90(), (3,): x90()),Cycle((0,): z(phi), (1,): z(phi), (2,): z(phi), (3,): z(phi)),Cycle((0,): Meas(), (1,): Meas(), (2,): Meas(), (3,): Meas(), marker=1))